In [1]:
# Google Colab related imports
import os
import importlib.util

if os.getenv("COLAB_RELEASE_TAG"):
   print("Running in Google Colab")
   # Install the easydiffraction library if it is not installed (including charts extras)
   if importlib.util.find_spec("easydiffraction") is None:
       !pip install 'easydiffraction[charts] @ git+https://github.com/easyscience/easydiffractionlib.git@new_job_dev'
   # Download the data files to be read in notebook
   if not os.path.exists('si.cif'): 
       !wget https://raw.githubusercontent.com/EasyScience/EasyDiffractionLib/refs/heads/new_job_dev/examples/Fitting_PD-TOF_Si-SEPD@Argonne/si.cif
   if not os.path.exists('sepd.xye'): 
       !wget https://raw.githubusercontent.com/EasyScience/EasyDiffractionLib/refs/heads/new_job_dev/examples/Fitting_PD-TOF_Si-SEPD@Argonne/sepd.xye

In [21]:
# Import the easydiffraction library
import easydiffraction as ed

## Job

In [22]:
# Create a job - the main object to store all the information
job = ed.Job(type='tof')

## Model

In [23]:
# Load a phase from CIF file
job.add_phase_from_file('si.cif')
print(job.phases)

Several values of it_coordinate_system_code have been defined:
2, 1
The default value has been choosen:'2'.
Several values of it_coordinate_system_code have been defined:
2, 1
The default value has been choosen:'2'.
Collection of 1 phases: ['si']


In [24]:
# Show phase info in CIF format
phase = job.phases['si']
print(phase.cif)

data_si
_cell_length_a 5.43146
_cell_length_b 5.43146
_cell_length_c 5.43146
_cell_angle_alpha 90.00000000
_cell_angle_beta 90.00000000
_cell_angle_gamma 90.00000000
_space_group_name_H-M_ref 'F d -3 m'
_space_group_IT_coordinate_system_code 2

loop_
_atom_site_label
_atom_site_type_symbol
_atom_site_fract_x
_atom_site_fract_y
_atom_site_fract_z
_atom_site_occupancy
_atom_site_adp_type
_atom_site_B_iso_or_equiv
Si Si 0.125 0.125 0.125 1.00000000 Biso 0.529


## Experiment

In [25]:
# Load experimentally measured data from a file in XYE format
job.add_experiment_from_file('sepd.xye')

In [26]:
pattern_params = job.pattern
experiment_params = job.parameters

In [27]:
job.show_experiment_chart()

# Analysis

In [28]:
# Display the analysis chart before setting initial parameter values
job.show_analysis_chart()

In [29]:
# Modify model-related parameters
phase.scale = 10
phase.cell.length_a = 5.43

# Modify experiment-related parameters
pattern_params.zero_shift = 0

experiment_params.dtt1 = 7476.91
experiment_params.dtt2 = -1.54
experiment_params.ttheta_bank = 144.845

experiment_params.alpha0 = 0.024
experiment_params.alpha1 = 0.204
experiment_params.beta0 = 0.038
experiment_params.beta1 = 0.011
experiment_params.sigma0 = 0
experiment_params.sigma1 = 0
experiment_params.sigma2 = 0

job.set_background([( 2000.0, 221.1),
                    ( 4000.0, 169.5),
                    ( 6000.0, 135.4),
                    (10000.0, 121.4),
                    (14000.0, 132.2),
                    (18000.0, 134.0),
                    (22000.0, 143.0),
                    (25000.0, 183.0),
                    (28000.0, 165.0),
                    (29995.0, 204.0)])

In [30]:
# Display the analysis chart after modifying parameters
job.show_analysis_chart()

In [31]:
# Select the model-related parameters to be fitted
phase.scale.free = True
phase.cell.length_a.free = True

# Select the experiment-related parameters to be fitted
pattern_params.zero_shift.free = True

experiment_params.sigma0.free = True
experiment_params.sigma1.free = True
experiment_params.sigma2.free = True

In [32]:
# Print parameters before fitting
job.print_free_parameters()

<Parameter 'scale': 10.0+/-0, bounds=[0:inf]>


In [33]:
# Start Least-Squares minimization to fit the selected parameters
job.fit(method='leastsq', tolerance=1e-4)

In [15]:
# Print parameters after fitting
job.print_free_parameters()

<Parameter 'scale': 12.65+/-0.08, bounds=[0:inf]>


In [16]:
# Display the analysis chart after fitting
job.show_analysis_chart()